# <center>Mini-Project: SVM & LR Classification</center>
<center><font size = "4"> 2017-2018 California Department of Education Mathmematics Achievement</font></center>

##### <center>Created by An Nguyen, Andy Ho, Jodi Pafford, Tori Wheelis</center>
<center> February 06, 2019</center>

In [33]:
import pandas as pd
import numpy as np
import datetime as dt
from __future__ import print_function
from sklearn.model_selection import ShuffleSplit
from sklearn.linear_model import LogisticRegression
from sklearn import metrics as mt

rainfall_original = pd.read_csv('weatherAus.csv') 

In [35]:
#functions to find the average value using the bracketing values around the NaN, will only use values if they are from the same city.
#if NaN is the earliest timepoint for a given city the next timepoint with no NaN will be given instead of the mean
#if NaN is the latest timepoint for a given city the previous timepoint with no NaN will be given instead of the mean

def impute_by_city(cities,variables):
    for c in cities:
        temp = rainfall[rainfall.Location == c] #parse out observations from a single city
        #interate through all observations of the temp data file
        i = min(temp.index)
        while i < max(temp.index):
            for v in variables:
                if pd.isna(temp[v]).all():
                    pass
                elif pd.isna(temp[v][i]):
                    temp[v][i] = find_mean(temp[v], i)
                    rainfall[v][i] = temp[v][i]
                    print(c, v)
            i = i + 1       

def find_mean(templist, index):
    if index == min(templist.index): #if earliest timepoint take the next value that is not NaN
        return find_top(templist, index)
    elif index == max(templist.index): #if latest timepoint take the previous value that is not NaN
        return find_bottom(templist, index)
    else:
        bottom = find_bottom(templist, index) #find previous non-NaN value
        top = find_top(templist, index) #find next non-NaN value
    if pd.isna(top): #if there are no more non-NaN values return the previous non-NaN value
        return bottom
    else:
        mean = (top + bottom)/2
        return mean

#find previous non-NaN value
def find_bottom(templist, index):
    while pd.isna(templist[index-1]):
        index = index-1
    bottom = templist[index-1]
    return bottom

#find next non-NaN value
#if there are no more non-NaN values return the previous non-NaN value
def find_top(templist, index):
    while pd.isna(templist[index+1]):
        index = index+1
        if index == max(templist.index):
            top = np.nan
            return top
    top = templist[index+1]
    return top          

In [36]:
rainfall = rainfall_original.copy()
rainfall.drop(["RISK_MM"], axis=1, inplace=True) #RISK_MM was used to extrapolate response variable.
rainfall['Date'] =  pd.to_datetime(rainfall['Date'], format='%Y-%m-%d') #change 'Date' variable to datetime64
rainfall.dropna(subset=["RainToday"], inplace=True) #drop any observation with no record of rainfall for the day, cannot be imputed
rainfall = rainfall.reset_index(drop=True) #reset the index after drops
rainfall.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 140787 entries, 0 to 140786
Data columns (total 23 columns):
Date             140787 non-null datetime64[ns]
Location         140787 non-null object
MinTemp          140319 non-null float64
MaxTemp          140480 non-null float64
Rainfall         140787 non-null float64
Evaporation      81093 non-null float64
Sunshine         73982 non-null float64
WindGustDir      131624 non-null object
WindGustSpeed    131682 non-null float64
WindDir9am       131127 non-null object
WindDir3pm       137117 non-null object
WindSpeed9am     139732 non-null float64
WindSpeed3pm     138256 non-null float64
Humidity9am      139270 non-null float64
Humidity3pm      137286 non-null float64
Pressure9am      127044 non-null float64
Pressure3pm      127018 non-null float64
Cloud9am         88162 non-null float64
Cloud3pm         84693 non-null float64
Temp9am          140131 non-null float64
Temp3pm          138163 non-null float64
RainToday        140787 non-n

In [37]:
#set the cardinal directions to degrees
directions = {'N':0, 'NNE':22.5, 'NE':45, 'NE':45, 'ENE':67.5, 'E':90, 'ESE':112.5, 'SE':135, 'SSE':157.5, 'S':180,\
              'SSW':202.5, 'SW':225, 'WSW':247.5, 'W':270, 'WNW':292.5, 'NW':315, 'NNW':337.5}
cities = rainfall.Location.unique() #get name of all cities in the data frame
c_variables = [] #variables with continuous values
d_variables = [] #variables with discreet values
        
rainfall = rainfall.replace(directions) #replace cardianl direction to their corresponding degrees

#change 'Yes' and 'No' to 1 and 0 respectively
rainfall.RainToday = rainfall.RainToday=='Yes'
rainfall.RainToday = rainfall.RainToday.astype(np.int)
rainfall.RainTomorrow = rainfall.RainTomorrow=='Yes'
rainfall.RainTomorrow = rainfall.RainTomorrow.astype(np.int)

for l in list(rainfall):
    if (rainfall[l].dtypes == 'float64'):
        c_variables.append(l)
    else:
        d_variables.append(l)

In [31]:
impute_by_city(cities, c_variables) #impute values to NaN 
rainfall.to_csv("rainfall.csv", sep=',', index=True) #save to csv for later use

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  # Remove the CWD from sys.path while we load stuff.
C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.
C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  # This is added back by InteractiveShellApp.in

Albury Cloud3pm
0
Albury Cloud9am
Albury Cloud3pm
1
Albury Cloud9am
2
Albury Cloud9am
Albury Cloud3pm
3
4
Albury Cloud9am
Albury Cloud3pm
5
Albury Cloud3pm
6
Albury Cloud9am
Albury Cloud3pm
7
Albury Cloud9am
Albury Cloud3pm
8
Albury Cloud9am
Albury Cloud3pm
9
Albury Cloud9am
Albury Cloud3pm
10
11
12
Albury Cloud9am
13
14
15
Albury Cloud9am
16
Albury Cloud9am
Albury Cloud3pm
17
Albury Cloud9am
Albury Cloud3pm
18
Albury Cloud9am
19
Albury Cloud9am
Albury Cloud3pm
20
Albury Cloud3pm
21
Albury Cloud9am
Albury Cloud3pm
22
Albury Cloud9am
23
Albury WindDir9am
Albury Cloud9am
24
Albury Cloud9am
Albury Cloud3pm
25
Albury Cloud9am
Albury Cloud3pm
26
27
Albury Cloud3pm
28
Albury Cloud9am
Albury Cloud3pm
29
Albury Cloud9am
Albury Cloud3pm
30
Albury Cloud9am
Albury Cloud3pm
31
Albury Cloud9am
Albury Cloud3pm
32
Albury Cloud9am
Albury Cloud3pm
33
Albury Cloud9am
Albury Cloud3pm
34
Albury Cloud9am
Albury Cloud3pm
35
Albury Cloud9am
Albury Cloud3pm
36
Albury Cloud9am
Albury Cloud3pm
37
Albury Cloud9a

Albury Cloud3pm
289
Albury Cloud9am
Albury Cloud3pm
290
291
292
Albury Cloud9am
293
294
295
296
Albury Cloud9am
297
Albury Cloud9am
Albury Cloud3pm
298
Albury Cloud9am
Albury Cloud3pm
299
Albury Cloud9am
Albury Cloud3pm
300
Albury Cloud9am
Albury Cloud3pm
301
302
Albury WindDir9am
Albury Cloud9am
303
Albury WindDir9am
Albury Cloud3pm
304
305
Albury WindDir9am
Albury Cloud9am
Albury Cloud3pm
306
Albury Cloud9am
Albury Cloud3pm
307
Albury Cloud9am
Albury Cloud3pm
308
Albury Cloud9am
Albury Cloud3pm
309
Albury Cloud9am
Albury Cloud3pm
310
Albury Cloud9am
311
312
313
314
Albury Cloud9am
315
Albury Cloud9am
316
Albury Cloud9am
317
Albury Cloud9am
Albury Cloud3pm
318
Albury Cloud9am
Albury Cloud3pm
319
Albury Cloud9am
Albury Cloud3pm
320
Albury Cloud9am
Albury Cloud3pm
321
Albury Cloud9am
Albury Cloud3pm
322
Albury Cloud9am
Albury Cloud3pm
323
Albury Cloud9am
Albury Cloud3pm
324
Albury Cloud9am
Albury Cloud3pm
325
Albury Cloud9am
Albury Cloud3pm
326
Albury Cloud9am
Albury Cloud3pm
327
Albury

Albury WindDir9am
Albury Cloud9am
Albury Cloud3pm
587
Albury Cloud9am
588
Albury WindDir9am
589
590
591
592
593
Albury WindDir9am
Albury Cloud9am
Albury Cloud3pm
594
595
Albury WindDir9am
Albury Cloud9am
596
Albury WindDir9am
Albury Cloud9am
597
Albury Cloud9am
Albury Cloud3pm
598
599
600
Albury Cloud3pm
601
Albury WindDir9am
602
Albury Cloud3pm
603
604
605
Albury WindDir9am
Albury Cloud9am
606
Albury WindDir9am
607
608
609
610
Albury Cloud9am
611
612
613
614
615
Albury Cloud9am
Albury Cloud3pm
616
617
618
Albury WindDir9am
Albury Cloud9am
Albury Cloud3pm
619
Albury Cloud9am
620
621
Albury WindDir9am
622
Albury Cloud9am
Albury Cloud3pm
623
624
625
626
Albury Cloud9am
627
Albury Cloud9am
628
629
630
Albury Cloud9am
631
Albury Cloud9am
632
Albury Cloud9am
633
Albury Cloud9am
Albury Cloud3pm
634
Albury Cloud9am
635
636
Albury Cloud9am
637
638
639
Albury Cloud9am
Albury Cloud3pm
640
Albury Cloud9am
Albury Cloud3pm
641
642
Albury WindDir9am
Albury Cloud3pm
643
644
Albury Cloud9am
645
Albury

Albury Cloud9am
909
910
911
Albury WindDir3pm
Albury Cloud9am
Albury Cloud3pm
912
913
Albury Cloud9am
914
Albury Cloud9am
Albury Cloud3pm
915
Albury WindDir9am
Albury Cloud9am
Albury Cloud3pm
916
Albury WindDir9am
Albury Cloud9am
917
Albury Cloud3pm
918
Albury Cloud9am
Albury Cloud3pm
919
Albury WindDir9am
Albury Cloud9am
Albury Cloud3pm
920
Albury Cloud9am
Albury Cloud3pm
921
Albury Cloud9am
Albury Cloud3pm
922
Albury Cloud9am
Albury Cloud3pm
923
Albury Cloud9am
Albury Cloud3pm
924
Albury WindDir9am
Albury Cloud9am
Albury Cloud3pm
925
Albury WindDir9am
Albury Cloud9am
Albury Cloud3pm
926
Albury WindDir9am
Albury Cloud9am
Albury Cloud3pm
927
Albury Cloud9am
Albury Cloud3pm
928
Albury Cloud9am
Albury Cloud3pm
929
Albury Cloud3pm
930
Albury Cloud9am
Albury Cloud3pm
931
Albury Cloud3pm
932
Albury Cloud9am
933
Albury Cloud9am
Albury Cloud3pm
934
Albury Cloud9am
Albury Cloud3pm
935
Albury Cloud9am
Albury Cloud3pm
936
Albury WindDir9am
Albury Cloud9am
Albury Cloud3pm
937
Albury WindDir9am
Al

...

Uluru Cloud3pm
139480
Uluru Cloud9am
Uluru Cloud3pm
139481
Uluru Cloud9am
Uluru Cloud3pm
139482
Uluru Cloud9am
Uluru Cloud3pm
139483
Uluru Cloud9am
Uluru Cloud3pm
139484
Uluru Cloud9am
Uluru Cloud3pm
139485
Uluru Cloud9am
Uluru Cloud3pm
139486
Uluru Cloud9am
Uluru Cloud3pm
139487
Uluru Cloud9am
Uluru Cloud3pm
139488
Uluru Cloud9am
Uluru Cloud3pm
139489
Uluru Cloud9am
Uluru Cloud3pm
139490
Uluru Cloud9am
Uluru Cloud3pm
139491
Uluru Cloud9am
Uluru Cloud3pm
139492
Uluru Cloud9am
Uluru Cloud3pm
139493
Uluru Cloud9am
Uluru Cloud3pm
139494
Uluru Cloud9am
Uluru Cloud3pm
139495
Uluru Cloud9am
Uluru Cloud3pm
139496
Uluru Cloud9am
Uluru Cloud3pm
139497
Uluru Cloud9am
Uluru Cloud3pm
139498
Uluru Cloud9am
Uluru Cloud3pm
139499
Uluru Cloud9am
Uluru Cloud3pm
139500
Uluru Cloud9am
Uluru Cloud3pm
139501
Uluru Cloud9am
Uluru Cloud3pm
139502
Uluru Cloud9am
Uluru Cloud3pm
139503
Uluru Cloud9am
Uluru Cloud3pm
139504
Uluru Cloud9am
Uluru Cloud3pm
139505
Uluru Cloud9am
Uluru Cloud3pm
139506
Uluru Cloud9am
U

Uluru Cloud9am
Uluru Cloud3pm
139702
Uluru Cloud9am
Uluru Cloud3pm
139703
Uluru Cloud9am
Uluru Cloud3pm
139704
Uluru Cloud9am
Uluru Cloud3pm
139705
Uluru Cloud9am
Uluru Cloud3pm
139706
Uluru Cloud9am
Uluru Cloud3pm
139707
Uluru Cloud9am
Uluru Cloud3pm
139708
Uluru Cloud9am
Uluru Cloud3pm
139709
Uluru Cloud9am
Uluru Cloud3pm
139710
Uluru Cloud9am
Uluru Cloud3pm
139711
Uluru Cloud9am
Uluru Cloud3pm
139712
Uluru Cloud9am
Uluru Cloud3pm
139713
Uluru Cloud9am
Uluru Cloud3pm
139714
Uluru Cloud9am
Uluru Cloud3pm
139715
Uluru Cloud9am
Uluru Cloud3pm
139716
Uluru Cloud9am
Uluru Cloud3pm
139717
Uluru Cloud9am
Uluru Cloud3pm
139718
Uluru Cloud9am
Uluru Cloud3pm
139719
Uluru Cloud9am
Uluru Cloud3pm
139720
Uluru Cloud9am
Uluru Cloud3pm
139721
Uluru Cloud9am
Uluru Cloud3pm
139722
Uluru Cloud9am
Uluru Cloud3pm
139723
Uluru Cloud9am
Uluru Cloud3pm
139724
Uluru Cloud9am
Uluru Cloud3pm
139725
Uluru Cloud9am
Uluru Cloud3pm
139726
Uluru Cloud9am
Uluru Cloud3pm
139727
Uluru Cloud9am
Uluru Cloud3pm
139728
1

Uluru Cloud9am
139991
139992
139993
139994
139995
Uluru Cloud9am
Uluru Cloud3pm
139996
Uluru Cloud9am
Uluru Cloud3pm
139997
Uluru Cloud9am
Uluru Cloud3pm
139998
Uluru Cloud9am
Uluru Cloud3pm
139999
Uluru Cloud9am
Uluru Cloud3pm
140000
Uluru Cloud9am
Uluru Cloud3pm
140001
Uluru Cloud9am
Uluru Cloud3pm
140002
Uluru Cloud9am
Uluru Cloud3pm
140003
Uluru Cloud9am
140004
Uluru Cloud9am
140005
Uluru Cloud9am
140006
Uluru Cloud9am
140007
Uluru Cloud9am
Uluru Cloud3pm
140008
Uluru Cloud3pm
140009
Uluru Cloud9am
Uluru Cloud3pm
140010
Uluru Cloud3pm
140011
Uluru Cloud9am
140012
Uluru Cloud3pm
140013
Uluru Cloud9am
Uluru Cloud3pm
140014
Uluru Cloud9am
Uluru Cloud3pm
140015
Uluru Cloud9am
Uluru Cloud3pm
140016
Uluru Cloud9am
Uluru Cloud3pm
140017
Uluru Cloud9am
Uluru Cloud3pm
140018
Uluru Cloud9am
Uluru Cloud3pm
140019
Uluru Cloud9am
Uluru Cloud3pm
140020
Uluru Cloud9am
Uluru Cloud3pm
140021
Uluru Cloud3pm
140022
Uluru Cloud3pm
140023
140024
Uluru Cloud9am
Uluru Cloud3pm
140025
Uluru Cloud9am
Uluru

Uluru WindDir9am
Uluru WindDir3pm
Uluru WindSpeed9am
Uluru WindSpeed3pm
Uluru Cloud9am
140280
Uluru WindGustDir
Uluru WindGustSpeed
Uluru WindDir9am
Uluru WindDir3pm
Uluru WindSpeed9am
Uluru WindSpeed3pm
140281
Uluru WindGustDir
Uluru WindGustSpeed
Uluru WindDir9am
Uluru WindDir3pm
Uluru WindSpeed9am
Uluru WindSpeed3pm
140282
Uluru WindGustDir
Uluru WindGustSpeed
Uluru WindDir9am
Uluru WindDir3pm
Uluru WindSpeed9am
Uluru WindSpeed3pm
140283
Uluru WindGustDir
Uluru WindGustSpeed
Uluru WindDir9am
Uluru WindDir3pm
Uluru WindSpeed9am
Uluru WindSpeed3pm
140284
Uluru WindGustDir
Uluru WindGustSpeed
Uluru WindDir9am
Uluru WindDir3pm
Uluru WindSpeed9am
Uluru WindSpeed3pm
Uluru Cloud9am
140285
Uluru WindGustDir
Uluru WindGustSpeed
Uluru WindDir9am
Uluru WindDir3pm
Uluru WindSpeed9am
Uluru WindSpeed3pm
Uluru Cloud9am
140286
Uluru Cloud9am
Uluru Cloud3pm
140287
Uluru Cloud9am
Uluru Cloud3pm
140288
Uluru Cloud9am
Uluru Cloud3pm
140289
Uluru Cloud9am
140290
Uluru Cloud9am
Uluru Cloud3pm
140291
Ulur

Uluru Cloud9am
140522
Uluru Cloud3pm
140523
Uluru Cloud9am
Uluru Cloud3pm
140524
Uluru Cloud9am
Uluru Cloud3pm
140525
Uluru Cloud9am
Uluru Cloud3pm
140526
Uluru Cloud9am
Uluru Cloud3pm
140527
Uluru Cloud9am
Uluru Cloud3pm
140528
Uluru Cloud9am
Uluru Cloud3pm
140529
Uluru Cloud9am
Uluru Cloud3pm
140530
Uluru Cloud9am
Uluru Cloud3pm
140531
Uluru Cloud9am
Uluru Cloud3pm
140532
Uluru Cloud9am
Uluru Cloud3pm
140533
Uluru Cloud9am
Uluru Cloud3pm
140534
Uluru Cloud9am
Uluru Cloud3pm
140535
Uluru Cloud9am
Uluru Cloud3pm
140536
Uluru Cloud9am
140537
Uluru Cloud9am
Uluru Cloud3pm
140538
Uluru Cloud9am
140539
Uluru Cloud9am
Uluru Cloud3pm
140540
140541
140542
Uluru Cloud9am
Uluru Cloud3pm
140543
Uluru Cloud9am
Uluru Cloud3pm
140544
Uluru Cloud9am
Uluru Cloud3pm
140545
Uluru Cloud9am
Uluru Cloud3pm
140546
140547
140548
140549
140550
140551
140552
140553
140554
Uluru Cloud3pm
140555
Uluru Cloud9am
Uluru Cloud3pm
140556
Uluru Cloud9am
Uluru Cloud3pm
140557
Uluru Cloud9am
Uluru Cloud3pm
140558
Uluru 

In [23]:
rainfall.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 140787 entries, 0 to 140786
Data columns (total 23 columns):
Date             140787 non-null datetime64[ns]
Location         140787 non-null object
MinTemp          140787 non-null float64
MaxTemp          140787 non-null float64
Rainfall         140787 non-null float64
Evaporation      86744 non-null float64
Sunshine         77574 non-null float64
WindGustDir      134802 non-null float64
WindGustSpeed    134802 non-null float64
WindDir9am       140780 non-null float64
WindDir3pm       139461 non-null float64
WindSpeed9am     140787 non-null float64
WindSpeed3pm     139462 non-null float64
Humidity9am      140787 non-null float64
Humidity3pm      138790 non-null float64
Pressure9am      128048 non-null float64
Pressure3pm      128048 non-null float64
Cloud9am         107222 non-null float64
Cloud3pm         104820 non-null float64
Temp9am          140787 non-null float64
Temp3pm          138790 non-null float64
RainToday        140787 